<a href="https://www.kaggle.com/code/mohammadalisafadoost/top-1000-universities-in-world-data-analyze?scriptVersionId=188655965" target="_blank"><img align="left" alt="Kaggle" title="Open in Kaggle" src="https://kaggle.com/static/images/open-in-kaggle.svg"></a>

<h1 style = " text-align:center; font-family:courier; font-size:250%; border: 1px solid; padding: 40px;" >
    <em>Top 1000 Universities in World Analyze</em>
</h1>

<hr />

<h4 style = " font-family:courier; " >
<p>
    In this notebook we are going to do some analyze on eighteen_nineteen_university_datasets.
</p>
</h4>

In [1]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from geopy.geocoders import Nominatim
import folium
from folium import FeatureGroup , CustomIcon
from folium.plugins import HeatMap
import warnings
# Ignore warnings
warnings.filterwarnings('ignore')
from tqdm.auto import tqdm
# Enable progress bar for pandas operations
tqdm.pandas()

In [2]:
pip install pycountry-convert

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.3/6.3 MB 65.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 233.8/233.8 kB 18.3 MB/s eta 0:00:00
Note: you may need to restart the kernel to use updated packages.


In [3]:
import pycountry_convert as pc

In [4]:
# Read the dataset
data = pd.read_csv(
    '/kaggle/input/eighteen-nineteen-university-datasets/eighteen_nineteen_university_datasets.csv',
    encoding='unicode_escape'
)
df = pd.DataFrame(data)

# Display the first few rows of the dataframe
df.head()

World Rank                            Institution        Location  \
0           1                     Harvard University             USA   
1           2                    Stanford University             USA   
2           3  Massachusetts Institute of Technology             USA   
3           4                University of Cambridge  United Kingdom   
4           5                   University of Oxford  United Kingdom   

   National Rank Quality of Education Alumni Employment Quality of Faculty  \
0              1                    2                 1                  1   
1              2                   10                 3                  2   
2              3                    3                11                  3   
3              1                    5                19                  6   
4              2                    9                25                 10   

  Research Output Quality Publications Influence Citations  Score  
0               1                    1         1         1  100.0  
1              10                    4         3         2   96.7  
2              30                   15         2         6   95.1  
3              12                    8         6        19   94.0  
4               9                    5         7         4   93.2

In [5]:
# Rename columns for better readability
df.columns = ['World_Rank','Institution','Country','National_Rank',
              'Quality_of_Education','Alumni_Employment','Quality_of_Faculty',
              'Research_Output','Quality_Publications','Influence','Citations','Score']

In [6]:
# Some dataset information
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1000 entries, 0 to 999
Data columns (total 12 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   World_Rank            1000 non-null   int64  
 1   Institution           1000 non-null   object 
 2   Country               1000 non-null   object 
 3   National_Rank         1000 non-null   int64  
 4   Quality_of_Education  1000 non-null   object 
 5   Alumni_Employment     1000 non-null   object 
 6   Quality_of_Faculty    1000 non-null   object 
 7   Research_Output       1000 non-null   object 
 8   Quality_Publications  1000 non-null   object 
 9   Influence             1000 non-null   object 
 10  Citations             1000 non-null   object 
 11  Score                 1000 non-null   float64
dtypes: float64(1), int64(2), object(9)
memory usage: 93.9+ KB


In [7]:
# Describe columns with numeric types
df.describe()

World_Rank  National_Rank        Score
count  1000.000000     1000.00000  1000.000000
mean    500.500000       40.02300    75.034300
std     288.819436       49.22871     4.670858
min       1.000000        1.00000    69.800000
25%     250.750000        6.00000    71.500000
50%     500.500000       21.00000    73.750000
75%     750.250000       51.00000    77.300000
max    1000.000000      213.00000   100.000000

In [8]:
# Describe other columns
df.drop(['World_Rank','National_Rank','Score'],axis=1).describe()

Institution Country Quality_of_Education  \
count                        1000    1000                 1000   
unique                       1000      61                  404   
top     Capital Normal University     USA                    -   
freq                            1     213                  597   

       Alumni_Employment Quality_of_Faculty Research_Output  \
count               1000               1000            1000   
unique               492                221             905   
top               > 1000                  -          > 1000   
freq                 509                731              77   

       Quality_Publications Influence Citations  
count                  1000      1000      1000  
unique                  892       830        75  
top                  > 1000    > 1000       898  
freq                     51       171       129

In [9]:
# Columns that must be numeric
numeric_cols = [col for col in df.columns if col not in ('Institution','Country')]

In [10]:
# Finding list of numbers that are missing in Quality_of_Education column
quality_of_education = df.loc[df['Quality_of_Education']!='-','Quality_of_Education']
quality_of_education = quality_of_education.astype('float64')
quality_of_education = quality_of_education.sort_values()
full_list = [i+1 for i in range(1000)]
missing_list_qoe = list(set(full_list)-set(quality_of_education))

In [11]:
# Def for fixing '-' values in Quality_of_Education column
def fix_dash_qoe(row,missing_list_iter) :
    if row['Quality_of_Education'] == '-' :
        return next(missing_list_iter)
    else :
        return row['Quality_of_Education']
qoe_missing_list_iter = iter(missing_list_qoe)

In [12]:
df['Quality_of_Education'] = df.apply(fix_dash_qoe , axis=1 , args=(qoe_missing_list_iter,))

In [13]:
# Finding list of numbers that are missing in Quality_of_Faculty column
quality_of_faculty = df.loc[df['Quality_of_Faculty']!='-','Quality_of_Faculty']
quality_of_faculty = quality_of_faculty.astype('float64')
quality_of_faculty = quality_of_faculty.sort_values()
missing_list_qof = list(set(full_list)-set(quality_of_faculty))

In [14]:
# Def for fixing '-' values in Quality_of_Faculty column
def fix_dash_qof(row,missing_list_iter) :
    if row['Quality_of_Faculty'] == '-' :
        return next(missing_list_iter)
    else :
        return row['Quality_of_Faculty']
qof_missing_list_iter = iter(missing_list_qof)

In [15]:
df['Quality_of_Faculty'] = df.apply(fix_dash_qof , axis=1 , args=(qof_missing_list_iter,))

In [16]:
# Def for fixing '> 1000' values in dataset
def fix_number(row,col) :
    if row[col] == '> 1000' :
        return 1001
    else :
        return row[col]

In [17]:
# Apply fix_number on all columns
for col in df.columns :
    df[f'{col}'] = df.apply(fix_number,axis=1,args=(f'{col}',))

In [18]:
# Change all numeric columns type to 'float64'
df[numeric_cols]=df[numeric_cols].astype('float64')
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1000 entries, 0 to 999
Data columns (total 12 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   World_Rank            1000 non-null   float64
 1   Institution           1000 non-null   object 
 2   Country               1000 non-null   object 
 3   National_Rank         1000 non-null   float64
 4   Quality_of_Education  1000 non-null   float64
 5   Alumni_Employment     1000 non-null   float64
 6   Quality_of_Faculty    1000 non-null   float64
 7   Research_Output       1000 non-null   float64
 8   Quality_Publications  1000 non-null   float64
 9   Influence             1000 non-null   float64
 10  Citations             1000 non-null   float64
 11  Score                 1000 non-null   float64
dtypes: float64(10), object(2)
memory usage: 93.9+ KB


<hr />

<h4 style = " font-family:courier; " >
<p>
    In above codes we checked dataset and there was some inappropriate data in dataset so we fixed them
</p>
</h4>

In [19]:
# Function to get country code from country name
def continent_name(row) :
    # Convert country name to country alpha-2 code
    country_code = pc.country_name_to_country_alpha2(row,cn_name_format="default")
    # Convert country alpha-2 code to continent code
    continent_name = pc.country_alpha2_to_continent_code(country_code)
    return continent_name

# Apply the continent_name function to the 'Country' column to create a new 'Continent' column
df['Continent'] = df['Country'].apply(continent_name)

# Dictionary to map continent codes to continent names
continents = {
    'NA': 'North America',
    'SA': 'South America', 
    'AS': 'Asia',
    'OC': 'Australia',
    'AF': 'Africa',
    'EU': 'Europe'
}

# Map the continent codes in the 'Continent' column to their full names
df['Continent'] = df['Continent'].map(continents)

In [20]:
# Create a figure object
fig = go.Figure()

# Add a line plot trace to the figure
fig.add_trace(go.Scatter(
    x=df['World_Rank'],
    y=df['Score'],
    mode='lines',
    name='Score VS World Rank'
))

# Create frames for animation
frames = [go.Frame(
    data = [go.Scatter(
        x=df['World_Rank'][:k+1],
        y=df['Score'][:k+1],
        mode='lines'
    )]
) for k in range(len(df))]

# Update the figure with frames for animation
fig.update(frames=frames)

# Update layout setting for the figure
fig.update_layout(
    xaxis=dict(range=[0,1000]), # Set x-axis range
    margin=dict(l=0, r=0, b=0, t=40), # Set margins
    title = dict(
        text='Universities World Rank VS Score',
        x=0.5,
        xanchor = 'center',
        font =dict(size=24)
    ), # Set title properties
    yaxis_title = 'Score',
    xaxis_title = 'World Rank',
    updatemenus=[dict(
        type='buttons',
        showactive=False,
        buttons=[dict(
            label='Play',
            method='animate',
            args=[None,dict(
                frame=dict(
                    duration=1, # Set frame duration for animation
                    redraw=True
                ),
                fromcurrent=True)]
        )]
    )]
)

# Display the figure
fig.show()

<hr />

<h4 style = " font-family:courier; " >
<p>
    In above chart you can see that most of top 1000 universities have score between 70 to 80 and there only about 50 with score greater than 85 , this shows us there is a huge difference between top universities with other universities .
</p>
</h4>

In [21]:
# Seperating top 100 universities for plotting
df_top_100 = df[df['World_Rank']<=100]
# Add a Value column with values between 0 and 1 for better slice view in sunburst chart
df_top_100['Value'] = (df_top_100['World_Rank'].mean())/(df_top_100['World_Rank']+df_top_100['World_Rank'].mean())

In [22]:
# Create a sunburst chart
fig = px.sunburst(
    df_top_100,
    path=['Continent','Country', 'Institution'],
    values='Value',
    color=df_top_100['Score'],
    hover_data=['World_Rank','National_Rank','Score'],
    color_continuous_scale=px.colors.sequential.Blackbody,
    range_color=(80,100)
)

# Update layout setting for the figure
fig.update_layout(
    height = 600, # Set the height of the figure
    margin=dict(l=0, r=0, b=0, t=40), # Set margins
    title = dict(
        text='Top 100 University in World seperated by their Continent and Countries',
        x=0.5,
        xanchor = 'center',
        font =dict(size=24)
    ) # Set title properties
)

# Display the figure
fig.show()

<hr />

<h4 style = " font-family:courier; " >
<p>
    In above chart you can see top 100 universities separated by their country and continent , as you can see most of them are in USA this shows us there is no better place for going to university than USA. 
</p>
</h4>

In [23]:
# Filter universities with scores >= 90
high_score = df[df['Score'] >= 90]

# Filter universities with scores between 80 and 90
mid_score = df[(df['Score'] < 90) & (df['Score'] >= 80)]

# Count universities by continent andcountry for scores >= 90
high_score_count = high_score.groupby(['Continent','Country']).size().reset_index(name = 'Count')

# Count universities by continent andcountry for scores between 80 and 90
mid_score_count = mid_score.groupby(['Continent','Country']).size().reset_index(name = 'Count')

# Sort the counts in desending order
high_score_count = high_score_count.sort_values(by='Count',ascending=False)
mid_score_count = mid_score_count.sort_values(by='Count',ascending=False)

# Create a bar chart for universities with score >= 90
fig_high = px.bar(
    high_score_count,
    x='Country',
    y='Count',
    color='Continent',
    title = 'Universities with Score >= 90',
    color_discrete_sequence=px.colors.sequential.Blackbody
)

# Display the bar chart
fig_high.show()

# Create a bar chart for universities with score between 80 and 90
fig_mid = px.bar(
    mid_score_count,
    x='Country',
    y='Count',
    color='Continent',
    title = 'Universities with Score 80-90',
    color_discrete_sequence=px.colors.sequential.Blackbody
)

# Display the bar chart
fig_mid.show()

<hr />

<h4 style = " font-family:courier; " >
<p>
    In first chart there are Countries with universities that have scores greater than 90 and in second chart there are Countries with universities that have scores between 80 and 90, each color in chart  also represent their continent. as we saw in previous chart USA has so much great universities and after that is UK from Europe</p>
</h4>

In [24]:
fig = px.box(
    df,
    x= 'Continent',
    y= 'Score',
    title= 'Distribution of University Scores by Continent',
    color_discrete_sequence=px.colors.sequential.Blackbody
)
fig.show()

<hr />

<h4 style = " font-family:courier; " >
<p>
    North America has highest median and South America and Africa have lowest median. there are a few universities with higher score from other universities are in most continents
</p>
</h4>

In [25]:
# Adding 'Latitude' and 'Longitude' columns to dataframe
df['Latitude'] = None
df['Longitude'] = None

In [26]:
# Create an instance of the Nominatim 
geolocator = Nominatim(user_agent='university_locator')

In [27]:
def get_coordinates(row) :
    # Try to get the location based on the university name
    try :
        location = geolocator.geocode(row['Institution'])
        return location.latitude,location.longitude
    except :
        # If the first attempt fails, try to get the location based on the country name
        try :
            location = geolocator.geocode(row['Country'])
            return location.latitude,location.longitude
        except :
            # If both attempts fail, return None for both latitude and longitude
            return None , None

In [28]:
# Apply the get_coordinates function to each row in the DataFrame
# The result is expanded into two new columns : 'Latitude' and 'Longitude'
df[['Latitude','Longitude']] = df.progress_apply(get_coordinates,axis = 1,
                                                 result_type = 'expand')

  0%|          | 0/1000 [00:00<?, ?it/s]

In [29]:
# Null counts in each column
df.isnull().sum()

World_Rank              0
Institution             0
Country                 0
National_Rank           0
Quality_of_Education    0
Alumni_Employment       0
Quality_of_Faculty      0
Research_Output         0
Quality_Publications    0
Influence               0
Citations               0
Score                   0
Continent               0
Latitude                0
Longitude               0
dtype: int64

In [30]:
# Grouping data by World Rank
group_1 = df[df['World_Rank'] < 10]
group_2 = df[(df['World_Rank'] >= 10) & (df['World_Rank'] < 100)]
group_3 = df[df['World_Rank'] >= 100]

# # Create a folium map centered around the mean latitude and longitude
rank_map = folium.Map(
    location=[
        df['Latitude'].mean(),
        df['Longitude'].mean()
    ],
    zoom_start=2
)

# Creating layer groups to show on map
fg1 = FeatureGroup(name='World Rank < 10')
fg2 = FeatureGroup(name='World Rank 10-100')
fg3 = FeatureGroup(name='World Rank >= 100')

# Adding locations to layer groups
for idx, row in group_1.iterrows() :
    icon = CustomIcon(
        icon_image = 'https://img.icons8.com/ios-filled/100/region-code.png' ,
        icon_size = (50,50)
    )
    folium.Marker(
        location=[row['Latitude'],row['Longitude']],
        popup="Name : "
            + str(row['Institution'])
            + "<br>"
            + "World Rank : "
            + str(row['World_Rank'])
            + "<br>"
            + "National Rank : "
            + str(row['National_Rank'])
            + "<br>"
            + "Country : "
            + str(row['Country'])
            + "<br>"
            + "Score : "
            + str(row['Score']),
        icon=icon
    ).add_to(fg1)
    
for idx, row in group_2.iterrows() :
    icon = CustomIcon(
        icon_image = 'https://img.icons8.com/color/96/visit.png',
        icon_size = (40,40)
    )
    folium.Marker(
        location=[row['Latitude'],row['Longitude']],
        popup="Name : "
            + str(row['Institution'])
            + "<br>"
            + "World Rank : "
            + str(row['World_Rank'])
            + "<br>"
            + "National Rank : "
            + str(row['National_Rank'])
            + "<br>"
            + "Country : "
            + str(row['Country'])
            + "<br>"
            + "Score : "
            + str(row['Score']),
        icon=icon
    ).add_to(fg2)
    
for idx, row in group_3.iterrows() :
    icon = CustomIcon(
        icon_image = 'https://img.icons8.com/color/96/region-code.png',
        icon_size = (30,30)
    )
    folium.Marker(
        location=[row['Latitude'],row['Longitude']],
        popup="Name : "
            + str(row['Institution'])
            + "<br>"
            + "World Rank : "
            + str(row['World_Rank'])
            + "<br>"
            + "National Rank : "
            + str(row['National_Rank'])
            + "<br>"
            + "Country : "
            + str(row['Country'])
            + "<br>"
            + "Score : "
            + str(row['Score']),
        icon=icon
    ).add_to(fg3)
    
fg1.add_to(rank_map)
fg2.add_to(rank_map)
fg3.add_to(rank_map)
folium.LayerControl().add_to(rank_map)

In [31]:
rank_map

<h4 style = " font-family:courier; " >
<p>
    In the map black signs shows top 10 universities , red ones show ranking between 10 and 100 and other signs are greater than 100.
</p>
</h4>

In [32]:
# Create a folium map centered around the mean latitude and longitude
heat_map = folium.Map(
    location=[
        df['Latitude'].mean(),
        df['Longitude'].mean()
    ],
    zoom_start=2
)

# Prepare the data for heatmap
heat_data = [[row['Latitude'],row['Longitude']] for index, row in df.iterrows()]

# Add the heatmap layer to folium map
HeatMap(heat_data).add_to(heat_map)
heat_map

<h4 style = " font-family:courier; " >
<p>
    You can see that density of universities in each region in this map.
</p>
</h4>